## Prevendo os preços do Petróleo Brent do IPEA

In [57]:
import pandas as pd
from utils import atualizando_dados_ipea

In [58]:
path = atualizando_dados_ipea()
dados = pd.read_csv(path)

In [59]:
dados.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11088 entries, 0 to 11087
Data columns (total 2 columns):
 #   Column                                Non-Null Count  Dtype  
---  ------                                --------------  -----  
 0   Data                                  11088 non-null  object 
 1   Preço - petróleo bruto - Brent (FOB)  11088 non-null  float64
dtypes: float64(1), object(1)
memory usage: 173.4+ KB


In [60]:
dados.tail()

Data  Preço - petróleo bruto - Brent (FOB)
11083  2024-01-10                                 78.46
11084  2024-01-11                                 80.21
11085  2024-01-12                                 79.89
11086  2024-01-15                                 79.76
11087  2024-01-16                                 80.15

In [61]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=dados['Data'], y=dados['Preço - petróleo bruto - Brent (FOB)'], name="Preço do Petróleo Brent"))
fig.layout.update(title_text='Preço do Petróleo Brent (FOB)', xaxis_rangeslider_visible=True)
fig.show()   


### Prophet

In [68]:
from plotly import graph_objs as go
from prophet import Prophet
from prophet.plot import plot_plotly
from prophet.serialize import model_from_json
import pickle

In [63]:
periodo = 7

df_train = dados[['Data','Preço - petróleo bruto - Brent (FOB)']]
df_train = df_train.rename(columns={"Data": "ds", "Preço - petróleo bruto - Brent (FOB)": "y"})

m = Prophet()
m.fit(df_train)
future = m.make_future_dataframe(periods=periodo, freq="B")
forecast = m.predict(future)

18:49:24 - cmdstanpy - INFO - Chain [1] start processing
18:49:31 - cmdstanpy - INFO - Chain [1] done processing


In [66]:
forecast.tail(periodo)

ds      trend  yhat_lower  yhat_upper  trend_lower  trend_upper  \
11088 2024-01-17  89.518580   74.589829  100.109476    89.518580    89.518580   
11089 2024-01-18  89.534364   74.634294   98.536984    89.534364    89.534364   
11090 2024-01-19  89.550148   74.858824   98.958118    89.550148    89.550148   
11091 2024-01-22  89.597501   75.723829   99.713338    89.597501    89.597501   
11092 2024-01-23  89.613285   75.631014   99.112923    89.613285    89.613285   
11093 2024-01-24  89.629070   74.332724   99.108703    89.629070    89.629070   
11094 2024-01-25  89.644854   74.377863   99.894661    89.644854    89.644854   

       additive_terms  additive_terms_lower  additive_terms_upper    weekly  \
11088       -2.555089             -2.555089             -2.555089 -0.132332   
11089       -2.448400             -2.448400             -2.448400 -0.046469   
11090       -2.411983             -2.411983             -2.411983 -0.026670   
11091       -2.373963             -2.373963             -2.373963 -0.013835   
11092       -2.449615             -2.449615             -2.449615 -0.090473   
11093       -2.493474             -2.493474             -2.493474 -0.132332   
11094       -2.411985             -2.411985             -2.411985 -0.046469   

       weekly_lower  weekly_upper    yearly  yearly_lower  yearly_upper  \
11088     -0.132332     -0.132332 -2.422758     -2.422758     -2.422758   
11089     -0.046469     -0.046469 -2.401931     -2.401931     -2.401931   
11090     -0.026670     -0.026670 -2.385313     -2.385313     -2.385313   
11091     -0.013835     -0.013835 -2.360128     -2.360128     -2.360128   
11092     -0.090473     -0.090473 -2.359142     -2.359142     -2.359142   
11093     -0.132332     -0.132332 -2.361142     -2.361142     -2.361142   
11094     -0.046469     -0.046469 -2.365516     -2.365516     -2.365516   

       multiplicative_terms  multiplicative_terms_lower  \
11088                   0.0                         0.0   
11089                   0.0                         0.0   
11090                   0.0                         0.0   
11091                   0.0                         0.0   
11092                   0.0                         0.0   
11093                   0.0                         0.0   
11094                   0.0                         0.0   

       multiplicative_terms_upper       yhat  
11088                         0.0  86.963490  
11089                         0.0  87.085964  
11090                         0.0  87.138165  
11091                         0.0  87.223538  
11092                         0.0  87.163670  
11093                         0.0  87.135596  
11094                         0.0  87.232869

In [71]:
with open('modelo/Prophet.pkl', "wb") as f:
    pickle.dump(m, f)

In [67]:
plot_plotly(m, forecast)

### Modelo 1